In [1]:
import scrapy
from scrapy.crawler import CrawlerProcess
import mysql.connector
from scrapy.spiders import Rule
from scrapy.spiders import CrawlSpider
from scrapy.linkextractors import LinkExtractor
from database_script import DatabaseHandler

collected_count = 0
categories = set()

In [2]:
class TabnakSpider(CrawlSpider):
    name = "tabnak_spider"
    allowed_domains = ["tabnak.ir"]
    start_urls = ["https://www.tabnak.ir/"]
    global categories
    
    rules = (Rule(LinkExtractor(allow=()), callback="parse", follow=True),)
    
    def __init__(self, *args, **kwargs):
        super(TabnakSpider, self).__init__(*args, **kwargs)
        self.db_handler = DatabaseHandler()
    
    def parse(self, response):
        
        global collected_count    
        
        if not self.is_news_url(response.url):
            return

        if collected_count >= 1000 and len(categories) >= 7 :
            raise scrapy.exceptions.CloseSpider("reached desired count")

        status_code = response.status
        if status_code != 200:
            self.log(f"Article URL {response.url} returned status code {status_code}. Skipping.")
            return
        
        if not self.extract_article_info(response):
            return
            
        news_id, title, category, content = self.extract_article_info(response)  
        
        self.db_handler.insert_data(news_id, title, category, content)
    
        collected_count += 1
        
        return {
            "count": collected_count,
            "news_id": news_id,
            "title": title,
            "category": category,
            "content" : content
        }
    
    def is_news_url(self, url):
        return "news" in url
    
    def extract_article_info(self, response):
        global categories
        content_arr = response.css("div.body p::text").getall()
        if content_arr == []:
            return False
        content= " ".join(content_arr)
        if len(content) < 300:
            self.log(f"Skipping news with content length less than 100 characters: {response.url}")
            return False
        
        news_id = response.css("span.news_id::text").get()
        
        if news_id == None:
             return False
        news_id= int(news_id)
        
        title = response.css("h1::text").get().strip()
        
        category_arr = response.css("div.news_path a::text").getall()
        if category_arr == []:
            return False
        category = category_arr[0].strip() if category_arr[0] != "صفحه نخست" else category_arr[1].strip()
        categories.add(category)
        
        return news_id, title, category, content
    
    def closed(self, reason):
        self.db_handler.close_connection()
    

In [3]:
process = CrawlerProcess()

process.crawl(TabnakSpider)

process.start()

2023-09-22 21:48:42 [scrapy.utils.log] INFO: Scrapy 2.8.0 started (bot: scrapybot)
2023-09-22 21:48:42 [scrapy.utils.log] INFO: Versions: lxml 4.9.3.0, libxml2 2.10.4, cssselect 1.1.0, parsel 1.6.0, w3lib 1.21.0, Twisted 22.10.0, Python 3.10.13 | packaged by Anaconda, Inc. | (main, Sep 11 2023, 13:24:38) [MSC v.1916 64 bit (AMD64)], pyOpenSSL 23.2.0 (OpenSSL 3.1.3 19 Sep 2023), cryptography 41.0.3, Platform Windows-10-10.0.22621-SP0
2023-09-22 21:48:42 [scrapy.crawler] INFO: Overridden settings:
{}
2023-09-22 21:48:42 [py.warnings] WARNING: C:\Users\FSG\projects\news_analysis_system\env\lib\site-packages\scrapy\utils\request.py:232: ScrapyDeprecationWarning: '2.6' is a deprecated value for the 'REQUEST_FINGERPRINTER_IMPLEMENTATION' setting.

It is also the default value. In other words, it is normal to get this warning if you have not defined a value for the 'REQUEST_FINGERPRINTER_IMPLEMENTATION' setting. This is so for backward compatibility reasons, but it will change in a future ver

2023-09-22 21:48:44 [scrapy.spidermiddlewares.offsite] DEBUG: Filtered offsite request to 'mlgn.to': <GET http://mlgn.to/27iz>
2023-09-22 21:48:44 [scrapy.dupefilters] DEBUG: Filtered duplicate request: <GET https://www.tabnak.ir/#tab3> - no more duplicates will be shown (see DUPEFILTER_DEBUG to show all duplicates)
2023-09-22 21:48:44 [scrapy.spidermiddlewares.offsite] DEBUG: Filtered offsite request to 't.me': <GET https://t.me/joinchat/AAAAAEEsII_zSxMKt05DLg>
2023-09-22 21:48:44 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET https://www.tabnak.ir/fa/contacts> from <GET http://www.tabnak.ir/fa/contacts>
2023-09-22 21:48:44 [scrapy.spidermiddlewares.offsite] DEBUG: Filtered offsite request to 'nabzebourse.com': <GET https://nabzebourse.com/>
2023-09-22 21:48:44 [scrapy.spidermiddlewares.offsite] DEBUG: Filtered offsite request to 'asiagrass.com': <GET https://asiagrass.com/>
2023-09-22 21:48:44 [scrapy.spidermiddlewares.offsite] DEBUG: Filtered offsite reques

2023-09-22 21:48:47 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET https://www.tabnak.ir/fa/economic> from <GET http://www.tabnak.ir/fa/economic>
2023-09-22 21:48:47 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET https://www.tabnak.ir/fa/world> from <GET http://www.tabnak.ir/fa/world>
2023-09-22 21:48:47 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET https://www.tabnak.ir/fa/sport> from <GET http://www.tabnak.ir/fa/sport>
2023-09-22 21:48:47 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.tabnak.ir/fa/news/1187197/%D8%AE%D8%A8%D8%B1%D9%86%DA%AF%D8%A7%D8%B1-%DA%86%D8%B7%D9%88%D8%B1-%D9%85%DB%8C%E2%80%8C%D8%AA%D9%88%D8%A7%D9%86%D8%AF-%D8%AC%D9%84%D9%88%DB%8C-%D8%AC%D8%B1%D9%85-%D8%B1%D8%A7-%D8%A8%DA%AF%DB%8C%D8%B1%D8%AF>
{'count': 1, 'news_id': 1187197, 'title': 'خبرنگار چطور می\u200cتواند جلوی جرم را بگیرد؟', 'category': 'فرهنگی', 'content': 'هر وقت از حرفه خبرنگاری سخن به میان می\u200cآید با توصیفا

2023-09-22 21:48:47 [scrapy.spidermiddlewares.offsite] DEBUG: Filtered offsite request to 'www.tabnakjavan.com': <GET http://www.tabnakjavan.com/>
2023-09-22 21:48:47 [scrapy.spidermiddlewares.offsite] DEBUG: Filtered offsite request to 'www.instagram.com': <GET http://www.instagram.com/tabnakjavan>
2023-09-22 21:48:47 [scrapy.spidermiddlewares.offsite] DEBUG: Filtered offsite request to 'www.t.me': <GET http://www.t.me/tabnakjavan>
2023-09-22 21:48:47 [scrapy.spidermiddlewares.offsite] DEBUG: Filtered offsite request to 'salamparvaz.com': <GET https://salamparvaz.com/tours/summer>
2023-09-22 21:48:47 [scrapy.spidermiddlewares.offsite] DEBUG: Filtered offsite request to 'kheiratnan.ir': <GET https://kheiratnan.ir/nan/>
2023-09-22 21:48:47 [scrapy.spidermiddlewares.offsite] DEBUG: Filtered offsite request to 'www.twitter.com': <GET https://www.twitter.com/home?status=%D8%AA%DA%A9%D9%84%DB%8C%D9%81%20%DA%A9%D9%86%DA%A9%D9%88%D8%B1%20%DB%B1%DB%B4%DB%B0%DB%B3%20%DA%86%D9%87%20%D9%85%DB%8C%

2023-09-22 21:48:48 [scrapy.spidermiddlewares.offsite] DEBUG: Filtered offsite request to 'lastsecond.ir': <GET https://lastsecond.ir/tours/%D8%AA%D9%88%D8%B1-%D8%AA%D8%B1%DA%A9%DB%8C%D9%87>
2023-09-22 21:48:48 [scrapy.spidermiddlewares.offsite] DEBUG: Filtered offsite request to 'hotelyar.com': <GET https://hotelyar.com/>
2023-09-22 21:48:48 [scrapy.spidermiddlewares.offsite] DEBUG: Filtered offsite request to 'rahbal.com': <GET https://rahbal.com/bus-ticket>
2023-09-22 21:48:48 [scrapy.spidermiddlewares.offsite] DEBUG: Filtered offsite request to 'www.iranhotelonline.com': <GET https://www.iranhotelonline.com/tehran-hotels/>
2023-09-22 21:48:48 [scrapy.spidermiddlewares.offsite] DEBUG: Filtered offsite request to 'cooldl.net': <GET http://cooldl.net/>
2023-09-22 21:48:48 [scrapy.spidermiddlewares.offsite] DEBUG: Filtered offsite request to 'arezoosafar.com': <GET https://arezoosafar.com/>
2023-09-22 21:48:48 [scrapy.spidermiddlewares.offsite] DEBUG: Filtered offsite request to 'vdigi

...

2023-09-22 21:55:34 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.tabnak.ir/fa/news/793431/%D8%B2%D9%85%D8%A7%D9%86-%D8%B1%D8%A7%D9%87%E2%80%8C%D8%A7%D9%86%D8%AF%D8%A7%D8%B2%DB%8C-%D9%86%D9%88%D8%A8%D8%AA%E2%80%8C%D8%AF%D9%87%DB%8C-%D8%A2%D9%86%D9%84%D8%A7%DB%8C%D9%86-%D9%85%D8%B9%D8%A7%DB%8C%D9%86%D9%87-%D9%81%D9%86%DB%8C> (referer: https://www.tabnak.ir/fa/news/795997/%D9%86%D8%A7%DA%AF%D9%81%D8%AA%D9%87%E2%80%8C%D9%87%D8%A7%DB%8C-%D8%B6%D8%B1%D8%BA%D8%A7%D9%85%DB%8C-%D8%A7%D8%B2-%D9%BE%D8%B4%D8%AA-%D9%BE%D8%B1%D8%AF%D9%87-%D9%85%D9%86%D8%A7%D8%B8%D8%B1%D9%87%E2%80%8C%D9%87%D8%A7-%D8%AA%D8%A7-%D8%AD%D8%B5%D8%B1)
2023-09-22 21:55:34 [scrapy.core.engine] DEBUG: Crawled (200) <GET https://www.tabnak.ir/fa/news/792916/%D9%BE%D8%A7%D8%B3%D8%AE-%D8%B3%DB%8C%D9%81-%D8%AE%D8%B7%D8%A7%D8%A8-%D8%A8%D9%87-%D9%85%D8%AA%D9%82%D8%A7%D8%B6%DB%8C%D8%A7%D9%86-%D8%A7%D8%B1%D8%B2> (referer: https://www.tabnak.ir/fa/news/792992/%D8%AC%D8%B2%DB%8C%DB%8C%D8%A7%D8%AA-%D9%88-%D9%86%D8%AD%D9%88%

2023-09-22 21:55:34 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.tabnak.ir/fa/news/794224/%D8%B6%D8%B1%D8%BA%D8%A7%D9%85%DB%8C-%D8%AD%D8%B5%D8%B1-%D8%A8%D9%87-%D9%87%DB%8C%DA%86%E2%80%8C%D9%88%D8%AC%D9%87-%D8%AA%D8%B5%D9%85%DB%8C%D9%85-%D8%B1%D9%87%D8%A8%D8%B1%DB%8C-%D9%86%D8%A8%D9%88%D8%AF>
{'count': 997, 'news_id': 794224, 'title': 'ضرغامی: حصر به هیچ\u200cوجه تصمیم رهبری نبود', 'category': 'سیاسی', 'content': 'ضرغامی در جمع زندانیان سیاسی رژیم سابق : «حصر را خیلی به رهبری وصل نکنید»«حصر تصمیم شورای عالی امنیت ملی کشور بود» «حصر را خیلی به رهبری وصل نکنید». این جمله را ضرغامی در جمع زندانیان سیاسی رژیم سابق گفته و در کانال شبکه پیام\u200cرسان داخلی\u200cاش منتشر کرده است. ضرغامی پیش\u200cتر در برنامه جهان\u200cآرا گفته بود: «حصر به\u200cهیچ\u200cوجه ارتباطی با مقام معظم رهبری نداشت و تصمیم شورای عالی امنیت ملی کشور بود». روزنامه شرق نوشت: او در همان جمع زندانیان سابق ادامه داده است: «مسئله «حصر» یک مسئله امنیتی است. همان\u200cطور که در سال ۸۹ با حضور آقای روحانی در جلسه

2023-09-22 21:55:34 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.tabnak.ir/fa/news/797451/%D8%AE%D8%B1%D9%88%D8%AC-%D8%A2%D9%85%D8%B1%DB%8C%DA%A9%D8%A7-%D8%A7%D8%B2-%D8%A8%D8%B1%D8%AC%D8%A7%D9%85-%D9%88-%D9%88%D8%A7%DA%A9%D9%86%D8%B4-%D8%A7%DB%8C%D8%B1%D8%A7%D9%86-%D8%A8%D9%87-%D8%A7%DB%8C%D9%86-%D8%A7%D8%AA%D9%81%D8%A7%D9%82-%D8%B1%D8%A7-%DA%86%DA%AF%D9%88%D9%86%D9%87-%D8%A7%D8%B1%D8%B2%DB%8C%D8%A7%D8%A8%DB%8C-%D9%85%DB%8C%E2%80%8C%DA%A9%D9%86%DB%8C%D8%AF>
{'count': 998, 'news_id': 797451, 'title': 'خروج آمریکا از برجام و واکنش ایران به این اتفاق را چگونه ارزیابی می\u200cکنید؟', 'category': 'سیاسی', 'content': 'سرانجام یک سال و اندی پس از به قدرت رسیدن دونالد ترامپ در ایالات متحده امریکا، رئیس\u200cجمهور ناراضی از برجام آمریکا از این معاهده بین\u200cالمللی خارج شد تا بعد از خروج از توافق\u200cنامه پاریس، آمریکای ترامپ عدم تعهد خود به یک قرارداد بین\u200cالمللی دیگر را هم نشان دهد. اظهارات شب گذشته ترامپ، واکنش\u200cهای فراوانی را در سرتاسر جهان داشت. اروپایی\u200cها لحظا

2023-09-22 21:55:35 [scrapy.core.scraper] DEBUG: Scraped from <200 https://www.tabnak.ir/fa/news/797479/%D8%A8%DB%8C%D8%A7%D9%86%DB%8C%D9%87-%D9%86%D9%85%D8%A7%DB%8C%D9%86%D8%AF%DA%AF%D8%A7%D9%86-%D8%AF%D8%B1-%D9%85%D8%AD%DA%A9%D9%88%D9%85%DB%8C%D8%AA-%D8%AE%D8%B1%D9%88%D8%AC-%D8%A2%D9%85%D8%B1%DB%8C%DA%A9%D8%A7-%D8%A7%D8%B2-%D8%A8%D8%B1%D8%AC%D8%A7%D9%85>
{'count': 1000, 'news_id': 797479, 'title': 'بیانیه نمایندگان در محکومیت خروج آمریکا از برجام', 'category': 'سیاسی', 'content': 'نمایندگان مجلس شورای اسلامی در بیانیه\u200cای به خروج آمریکا از برجام واکنش نشان داده و بیان کردند جمهوری اسلامی ایران همواره ضمن تاکید بر صیانت از حقوق هسته\u200cای خود بر عنصر دیپلماسی و تعامل با دنیا تاکید کرده است و در این عرصه نیز یک بار دیگر حقانیت ملت ایران ثابت شد. به گزارش ایسنا، متن این بیانیه که توسط علی\u200cاکبر رنجبرزاده عضو هیات رییسه قرائت شد، به شرح زیر است: «ملت عظیم\u200cالشان ایران اسلامی، رییس\u200cجمهور گستاخ ایالات متحده آمریکا برخلاف قواعد بین\u200cالمللی از برجام خارج شد و نشان داد 

2023-09-22 21:55:35 [scrapy.core.engine] DEBUG: Crawled (403) <GET https://www.tabnak.ir/fa/save/797429> (referer: https://www.tabnak.ir/fa/news/797429/%D8%A8%D8%A7%D9%82%D8%B1%DB%8C-%D8%A8%D8%B1%D8%AC%D8%A7%D9%85-%D8%A7%D8%B2-%D8%A7%D9%88%D9%84-%D9%87%D9%85-%D9%85%D8%B7%D9%84%D9%88%D8%A8-%D9%85%D9%84%D8%AA-%D9%85%D8%A7-%D9%86%D8%A8%D9%88%D8%AF-%D9%85%D9%88%D8%B3%D9%88%DB%8C%D8%AE%D8%AF%D8%A7-%D8%B1%D8%A7-%D8%B4%DA%A9%D8%B1-%D8%AC%D8%B9%D9%81%D8%B1%DB%8C-%D8%B1%D9%88%D8%B4%D9%86-%D8%A7%D8%B3%D8%AA-%DA%A9%D9%87-%D8%A7%D8%B1%D9%88%D9%BE%D8%A7%DB%8C%DB%8C%E2%80%8C%D9%87%D8%A7-%D9%86%D9%85%DB%8C%E2%80%8C%D8%AA%D9%88%D8%A7%D9%86%D9%86%D8%AF-%D9%85%D8%B3%D8%AA%D9%82%D9%84%D8%A7%D9%86%D9%87-%D8%AA%D8%B5%D9%85%DB%8C%D9%85-%D8%A8%DA%AF%DB%8C%D8%B1%D9%86%D8%AF-%D8%B3%D8%B1%D9%86%D9%88%D8%B4%D8%AA-%D8%A8%D8%B1%D8%AC%D8%A7%D9%85-%D8%B1%D9%88%D8%B4%D9%86-%D8%A7%D8%B3%D8%AA) ['partial']
2023-09-22 21:55:35 [scrapy.downloadermiddlewares.redirect] DEBUG: Redirecting (301) to <GET https://www.tabnak.ir